In [2]:
import requests
import time
import pandas as pd

In [2]:
url_p = 'https://www.reddit.com/r/progressive.json'
url_c = 'https://www.reddit.com/r/Conservative.json'

In [4]:
headers = {'User-agent':'Bleep blot blort 0.11'}

In [5]:
res_p = requests.get(url_p, headers=headers)
res_c = requests.get(url_c, headers=headers)

In [11]:
dict_p = res_p.json()
dict_c = res_c.json()

In [34]:
p_posts = []
after = None

for i in range(100):
    print(i)
    if after == None:
        params = {}
    else:
        params = {'after':after}
    
    res = requests.get(url_p, params=params, headers=headers)
    dict_p = res.json()
    p_posts.extend(dict_p['data']['children'])
    after = dict_p['data']['after']
    
    time.sleep(10)
    

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99


In [36]:
p_posts

[{'kind': 't3',
  'data': {'approved_at_utc': None,
   'subreddit': 'progressive',
   'selftext': '',
   'author_fullname': 't2_38lau',
   'saved': False,
   'mod_reason_title': None,
   'gilded': 0,
   'clicked': False,
   'title': "Acosta, Who Cut Deal With Epstein, Tried to Slash Anti-Trafficking Program by 80 Percent: “How can we expect you, the Labor Secretary to fight for American workers if you couldn't even fight for these girls?”",
   'link_flair_richtext': [],
   'subreddit_name_prefixed': 'r/progressive',
   'hidden': False,
   'pwls': None,
   'link_flair_css_class': None,
   'downs': 0,
   'thumbnail_height': 78,
   'hide_score': False,
   'name': 't3_cbhfme',
   'quarantine': False,
   'link_flair_text_color': 'dark',
   'author_flair_background_color': None,
   'subreddit_type': 'public',
   'ups': 265,
   'total_awards_received': 0,
   'media_embed': {},
   'thumbnail_width': 140,
   'author_flair_template_id': None,
   'is_original_content': False,
   'user_reports': [

In [40]:
df_p = pd.DataFrame(p_posts)

In [110]:
# Create a list of  progressive documents

prog = []
for i in range(2448):
    prog.append(df_p['data'][i]['title'])

In [114]:
# instantiate progressive corpus by rendering list as DataFrame

prog_df = pd.DataFrame(prog)

In [121]:
# labeling documents with their source, p=1, c=0

prog_df['source'] = 1

In [39]:
c_posts = []
after = None
for i in range(100):
    print(i)
    if after == None:
        params = {}
    else:
        params = {'after':after}
        
    res = requests.get(url_c, params=params, headers=headers)
    dict_c = res.json()
    c_posts.extend(dict_c['data']['children'])
    after = dict_c['data']['after']
    
    time.sleep(5)

0
1
2
3
4
5
6
7
8
9
10
11
12
13
14
15
16
17
18
19
20
21
22
23
24
25
26
27
28
29
30
31
32
33
34
35
36
37
38
39
40
41
42
43
44
45
46
47
48
49
50
51
52
53
54
55
56
57
58
59
60
61
62
63
64
65
66
67
68
69
70
71
72
73
74
75
76
77
78
79
80
81
82
83
84
85
86
87
88
89
90
91
92
93
94
95
96
97
98
99


In [95]:
df_c = pd.DataFrame(c_posts)

In [116]:
df_c.shape

(2448, 2)

In [117]:
# Create a list of  conservative documents

cons = []
for i in range(2448):
    cons.append(df_c['data'][i]['title'])

In [118]:
# instantiate conservative corpus by rendering list as DataFrame

cons_df = pd.DataFrame(cons)

In [119]:
# labeling documents with their source, p=1, c=0

cons_df['source'] = 0

In [122]:
# Create master DataFrame, with just progressive/conservative corpora matched with their labels

df = prog_df.append(cons_df)

In [126]:
df.shape

(4896, 2)

In [127]:
df['source'].unique()

array([1, 0])

# Data munging complete, corpus of ~5k labeled documents

In [129]:
df.to_csv('./initialcorpus.csv', index=False)

In [3]:
df = pd.read_csv('./initialcorpus.csv')

# Onto preprocessing data for NLP

In [4]:
import nltk
from nltk.stem import WordNetLemmatizer
from nltk.tokenize import RegexpTokenizer
from sklearn.feature_extraction.text import CountVectorizer, TfidfVectorizer
from sklearn.pipeline import Pipeline
from sklearn.model_selection import train_test_split, GridSearchCV
from sklearn.linear_model import LogisticRegression
from sklearn.naive_bayes import MultinomialNB
from sklearn.metrics import confusion_matrix

In [5]:
# baseline model: No issue with prior probability

df['source'].value_counts(normalize=True)

1    0.5
0    0.5
Name: source, dtype: float64

In [17]:
df['0']

0       Acosta, Who Cut Deal With Epstein, Tried to Sl...
1       Bernie's Right: 3 Billionaires Have More Wealt...
2       Democratic challenger to Susan Collins announc...
3       Mueller Missed the Crime: Trump Team Coordinat...
4       Chronic nuisance ordinances are forcing people...
5       Trump’s July Fourth event and weekend protests...
6       Federal judge says DOJ can't swap out its lega...
7       The comeback state of 2019: Kansas economy reb...
8       Segregation has soared in America’s schools as...
9            Any email list too progressives in Congress?
10      A Democratic Think Tank, the Progressive Polic...
11      Man charged with brutal stabbing told police t...
12      Gov. Cuomo approves new law allowing release o...
13      Antivaxxers turn to homeschooling to avoid pro...
14      Trump officials tell one court Obamacare is fa...
15      5 Revelations From Children in Border Patrol F...
16      A federal program to help injured veterans and...
17            

In [133]:
X = df[0]
y = df['source']

In [134]:
X_train, X_test, y_train, y_test = train_test_split(X, y)

In [247]:
# pipeline for Count Vectorized logistic regression

pipe_cv_lr = Pipeline([('cvec', CountVectorizer()),
                           ('lr', LogisticRegression())
                       ])

In [145]:
# pipeline for Count Vectorized MultiNomial Naive Bayes model

pipe_cv_mnb = Pipeline([('cvec', CountVectorizer()),
                        ('mnb', MultinomialNB())
                    ])

In [248]:
# pipeline for TFIDF vectorized logistic regression

pipe_tvec_lr = Pipeline([('tvec', TfidfVectorizer()),
                             ('lr', LogisticRegression())
                             ])

In [150]:
# pipeline for TFIDF vectorized logistic regression

pipe_tvec_mnb = Pipeline([('tvec', TfidfVectorizer()),
                          ('mnb', MultinomialNB())
                          ])

In [249]:
# gridsearching through Count Vectorized logistic regression

pipe_params_cvec_lr = {
    'cvec__max_features': [5000],
    'cvec__min_df': [2, 3],
    'cvec__max_df': [.9, .95],
    'cvec__ngram_range': [(1,1), (1,2), (1,3)],
    'cvec__stop_words': [None, 'english'],
    
}

gs_cv_lr = GridSearchCV(pipe_cv_lr, param_grid=pipe_params_cvec_lr, cv=3)
gs_cv_lr.fit(X_train, y_train)
print(gs_cv_lr.best_score_)
gs_cv_lr.best_params_

/Users/mikhaillenko/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)


0.9281045751633987


{'cvec__max_df': 0.9,
 'cvec__max_features': 5000,
 'cvec__min_df': 2,
 'cvec__ngram_range': (1, 2),
 'cvec__stop_words': None}

In [250]:
print(gs_cv_lr.score(X_train, y_train))
print(gs_cv_lr.score(X_test, y_test))

0.9953703703703703
0.9795751633986928


In [251]:
y_pred_cv_lr = gs_cv_lr.predict(X_test)
cm_cv_lr = confusion_matrix(y_test, y_pred_cv_lr)

In [252]:
cm_cv_lr = pd.DataFrame(data=cm_cv_lr,
                     index=['Actual Negatives','Actual Positives'],
                     columns=['Predicted Negatives','Predicted Positives'])
cm_cv_lr

Predicted Negatives  Predicted Positives
Actual Negatives                  587                   13
Actual Positives                   12                  612

In [222]:
# gridsearching through Count Vectorized multinominal naive Bayes

pipe_params_cvec_mnb = {
    'cvec__max_features': [4500,5000],
    'cvec__min_df': [2, 3],
    'cvec__max_df': [.9, .95],
    'cvec__ngram_range': [(1,1), (1,2)],
    'cvec__stop_words': [None, 'english']
}

gs_cv_mnb = GridSearchCV(pipe_cv_mnb, param_grid=pipe_params_cvec_mnb, cv=3)
gs_cv_mnb.fit(X_train, y_train)
print(gs_cv_mnb.best_score_)
gs_cv_mnb.best_params_

0.8627450980392157


{'cvec__max_df': 0.9,
 'cvec__max_features': 4500,
 'cvec__min_df': 2,
 'cvec__ngram_range': (1, 1),
 'cvec__stop_words': 'english'}

In [227]:
print(gs_cv_mnb.score(X_train, y_train))
print(gs_cv_mnb.score(X_test, y_test))

0.9645969498910676
0.9027777777777778


In [236]:
y_pred_cv_mnb = gs_cv_mnb.predict(X_test)
cm_cv_mnb = confusion_matrix(y_test, y_pred_cv_mnb)

In [237]:
cm_cv_mnb = pd.DataFrame(data=cm_cv_mnb,
                     index=['Actual Negatives','Actual Positives'],
                     columns=['Predicted Negatives','Predicted Positives'])
cm_cv_mnb

Predicted Negatives  Predicted Positives
Actual Negatives                  523                   77
Actual Positives                   42                  582

In [254]:
# gridsearching through TFIDF logistic regression

pipe_params_tvec_lr = {
    'tvec__max_features': [4500,5000],
    'tvec__min_df': [2, 3],
    'tvec__max_df': [.9, .95],
    'tvec__ngram_range': [(1,1), (1,2), (1,3)],
    'tvec__stop_words': [None, 'english']
}

gs_tvec_lr = GridSearchCV(pipe_tvec_lr, param_grid=pipe_params_tvec_lr, cv=3)
gs_tvec_lr.fit(X_train, y_train)
print(gs_tvec_lr.best_score_)
gs_tvec_lr.best_params_

/Users/mikhaillenko/anaconda3/lib/python3.6/site-packages/sklearn/linear_model/logistic.py:432: FutureWarning: Default solver will be changed to 'lbfgs' in 0.22. Specify a solver to silence this warning.
  FutureWarning)


0.8929738562091504


{'tvec__max_df': 0.9,
 'tvec__max_features': 5000,
 'tvec__min_df': 2,
 'tvec__ngram_range': (1, 2),
 'tvec__stop_words': 'english'}

In [1]:
print(gs_tvec_lr.score(X_train, y_train))
print(gs_tvec_lr.score(X_test, y_test))

NameError: name 'gs_tvec_lr' is not defined

In [256]:
y_pred_tvec_lr = gs_tvec_lr.predict(X_test)
cm_tvec_lr = confusion_matrix(y_test, y_pred_tvec_lr)

cm_tvec_lr = pd.DataFrame(data=cm_tvec_lr,
                     index=['Actual Negatives','Actual Positives'],
                     columns=['Predicted Negatives','Predicted Positives'])
cm_tvec_lr

Predicted Negatives  Predicted Positives
Actual Negatives                  555                   45
Actual Positives                   35                  589

In [257]:
# gridsearching through TFIDF Multinomial Naive Bayes

pipe_params_tvec_mnb = {
    'tvec__max_features': [4500,5000],
    'tvec__min_df': [2, 3],
    'tvec__max_df': [.9, .95],
    'tvec__ngram_range': [(1,1), (1,2), (1,3)],
    'tvec__stop_words': [None, 'english']
}

gs_tvec_mnb = GridSearchCV(pipe_tvec_mnb, param_grid=pipe_params_tvec_mnb, cv=3)
gs_tvec_mnb.fit(X_train, y_train)
print(gs_tvec_mnb.best_score_)
gs_tvec_mnb.best_params_

0.8760893246187363


{'tvec__max_df': 0.9,
 'tvec__max_features': 5000,
 'tvec__min_df': 2,
 'tvec__ngram_range': (1, 2),
 'tvec__stop_words': 'english'}

In [240]:
print(gs_tvec_mnb.score(X_train, y_train))
print(gs_tvec_mnb.score(X_test, y_test))

0.960511982570806
0.8946078431372549


In [241]:
y_pred_tvec_mnb = gs_tvec_mnb.predict(X_test)
cm_tvec_mnb = confusion_matrix(y_test, y_pred_tvec_mnb)

cm_tvec_mnb = pd.DataFrame(data=cm_tvec_mnb,
                     index=['Actual Negatives','Actual Positives'],
                     columns=['Predicted Negatives','Predicted Positives'])
cm_tvec_mnb

Predicted Negatives  Predicted Positives
Actual Negatives                  536                   64
Actual Positives                   65                  559

In [286]:
cvec = CountVectorizer(X_train,
                       max_df=0.9,
                       max_features=5000,
                       min_df=2,
                       ngram_range=(1, 2),
                       stop_words=None)

# X_train_vec = cvec.fit_transform(X_train)
# X_test_vec = cvec.fit_transform(X_test)

In [283]:
len(list(X_train))

3672

In [290]:
X_train = pd.DataFrame(X_train)

In [291]:
type(X_train)

pandas.core.frame.DataFrame

In [295]:
X_train_fit = cvec.transform(X_train)

NotFittedError: CountVectorizer - Vocabulary wasn't fitted.